# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO)

Installing required packages and dependencies

In [ ]:
%%capture
!pip install py-elvis
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido

!pip install stable-baselines3[extra]
!pip install stable-baselines
!pip install sb3-contrib
!pip install gym
!pip install -q wandb

In [ ]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [ ]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.21.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.21.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.21.0\n')
wandb, version 0.13.4


In [ ]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [ ]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 65% average battery) 
#case = 'wohnblock_household_simulation_adaptive_18.yaml' #(18 EVs arrivals per week with 40% average battery) 
#case = 'wohnblock_household_simulation_adaptive_22.yaml' #(22 EVs arrivals per week with 55% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f7613258cd0>Mean parking time: 23.9
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.9, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_energy

In [ ]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_ELVIS_data()

In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21594.18 , over-consume=kWh  38914.26 , under-consume=kWh  17320.08 , Total_cost=€  871.26 , overcost=€  1370.15 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [ ]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [ ]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  22515.62 , over-consume=kWh  39516.73 , under-consume=kWh  17001.11 , Total_cost=€  868.44 , overcost=€  1372.16 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -3540.52 , over-consume=KWh  1981.36 , under-consume=KWh  5521.88 , Total_cost=€  -76.13 , Overcost=€  69.39 
 EV_INFO: Av.EV_energy_leaving=kWh  67.04 , Std.EV_energy_leaving=kWh  24.1 , EV_departures =  1042 , EV_queue_left =  0
SCORE:  Cumulative_reward= 417408.23 - Step_rewars (load_t= 376044.3, EVs_energy_t= 17368.67)
 - Final_rewards (EVs_energy= 17174.03, Overconsume= -1230.2, Underconsume= -2339.91, Overcost= 10391.34)
Episode:1 Score:417408.2343370361


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1    2    3              EVs_id  \
time                                                                      
2022-01-01 00:00:00  41.208797  43.412567  0.0  0.0        [0, 0, 0, 0]   
2022-01-01 00:15:00  41.458797  42.627151  0.0  0.0  [3129, 3128, 0, 0]   
2022-01-01 00:30:00  41.708797  41.735939  0.0  0.0  [3129, 3128, 0, 0]   
2022-01-01 00:45:00  41.958797  41.010906  0.0  0.0  [3129, 3128, 0, 0]   
2022-01-01 01:00:00  42.208797  40.486069  0.0  0.0  [3129, 3128, 0, 0]   
...                        ...        ...  ...  ...                 ...   
2022-06-06 04:45:00  92.770775  69.160896  0.0  0.0  [3569, 3568, 0, 0]   
2022-06-06 05:00:00  94.344521  70.734642  0.0  0.0  [3569, 3568, 0, 0]   
2022-06-06 05:15:00  95.891663  72.281784  0.0  0.0  [3569, 3568, 0, 0]   
2022-06-06 05:30:00  97.333046  73.723167  0.0  0.0  [3569, 3568, 0, 0]   
2022-06-06 05:45:00  98.595802  74.985924  0.0  0.0  [3569, 3568, 0, 0]   

                          actions                    mask_truth          load  \
time                                                                            
2022-01-01 00:00:00  [1, 2, 2, 2]  [False, False, False, False]  2.260476e+00   
2022-01-01 00:15:00  [1, 2, 2, 2]   [False, True, False, False]  0.000000e+00   
2022-01-01 00:30:00  [1, 2, 2, 2]   [False, True, False, False]  0.000000e+00   
2022-01-01 00:45:00  [1, 2, 2, 2]   [False, True, False, False]  0.000000e+00   
2022-01-01 01:00:00  [1, 2, 2, 2]   [False, True, False, False] -2.220446e-16   
...                           ...                           ...           ...   
2022-06-06 04:45:00  [1, 1, 2, 2]   [False, True, False, False]  0.000000e+00   
2022-06-06 05:00:00  [1, 1, 2, 2]   [False, True, False, False]  0.000000e+00   
2022-06-06 05:15:00  [1, 1, 2, 2]   [False, True, False, False]  0.000000e+00   
2022-06-06 05:30:00  [1, 1, 2, 2]   [False, True, False, False]  0.000000e+00   
2022-06-06 05:45:00  [1, 1, 2, 2]   [False, True, False, False]  0.000000e+00   

                     load_reward  EV_reward    rewards  
time                                                    
2022-01-01 00:00:00    15.000000        0.0  15.000000  
2022-01-01 00:15:00    15.000000        0.0  15.000000  
2022-01-01 00:30:00    15.000000        0.0  15.000000  
2022-01-01 00:45:00    15.000000        0.0  15.000000  
2022-01-01 01:00:00    15.000000        0.0  15.000000  
...                          ...        ...        ...  
2022-06-06 04:45:00    15.000000        0.0  15.000000  
2022-06-06 05:00:00    15.000000        0.0  15.000000  
2022-06-06 05:15:00    15.000000        0.0  15.000000  
2022-06-06 05:30:00    15.000000        0.0  15.000000  
2022-06-06 05:45:00     3.527543        0.0   3.527543  

[15000 rows x 11 columns]

In [ ]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [ ]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 4173, Arrival time: 2022-01-01 07:00:00, Parking_time: 24, Leaving_time: 2022-01-02 07:00:00, SOC: 0.5134465085438495, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 5215, Arrival time: 2022-12-31 11:00:00, Parking_time: 23.734689285904096, Leaving_time: 2023-01-01 10:44:04.881429, SOC: 0.2901617981550553, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  11947.09 , over-consume=kWh  33663.79 , under-consume=kWh  21716.7 , Total_cost=€  608.73 , overcost=€  1498.53 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12404.92 , over-consume=kWh  34186.65 , under-consume=kWh  21781.73 , Total_cost=€  600.63 , overcost=€  1492.24 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -7361.31 , over-consume=KWh  1224.57 , under-consume=KWh  8585.89 , Total_cost=€  -274.21 , Overcost=€  54.53 
 EV_INFO: Av.EV_energy_leaving=kWh  71.76 , Std.EV_energy_leaving=kWh  23.39 , EV_departures =  1041 , EV_queue_left =  0
SCORE:  Cumulative_reward= 409222.0 - Step_rewars (load_t= 350721.56, EVs_energy_t= 31557.18)
 - Final_rewards (EVs_energy= 18172.53, Overconsume= -645.72, Underconsume= -3640.85, Overcost= 13057.31)
Episode:1 Score:409222.00328317686


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0    1    2          3              EVs_id  \
time                                                                      
2022-01-01 00:00:00   0.000000  0.0  0.0   0.000000        [0, 0, 0, 0]   
2022-01-01 00:15:00   0.000000  0.0  0.0   0.000000        [0, 0, 0, 0]   
2022-01-01 00:30:00   0.000000  0.0  0.0   0.000000        [0, 0, 0, 0]   
2022-01-01 00:45:00   0.000000  0.0  0.0   0.000000        [0, 0, 0, 0]   
2022-01-01 01:00:00   0.000000  0.0  0.0   0.000000        [0, 0, 0, 0]   
...                        ...  ...  ...        ...                 ...   
2022-06-06 04:45:00  59.825535  0.0  0.0  59.314129  [6706, 0, 0, 6707]   
2022-06-06 05:00:00  61.015320  0.0  0.0  60.503914  [6706, 0, 0, 6707]   
2022-06-06 05:15:00  62.264420  0.0  0.0  61.753014  [6706, 0, 0, 6707]   
2022-06-06 05:30:00  63.486042  0.0  0.0  62.974636  [6706, 0, 0, 6707]   
2022-06-06 05:45:00  64.618355  0.0  0.0  64.106949  [6706, 0, 0, 6707]   

                          actions                   mask_truth      load  \
time                                                                       
2022-01-01 00:00:00  [2, 1, 1, 0]  [False, False, False, True] -3.656257   
2022-01-01 00:15:00  [2, 1, 1, 0]  [False, False, False, True] -4.188789   
2022-01-01 00:30:00  [2, 0, 1, 0]   [False, True, False, True] -4.945215   
2022-01-01 00:45:00  [2, 1, 1, 0]  [False, False, False, True] -2.553009   
2022-01-01 01:00:00  [2, 0, 1, 0]   [False, True, False, True] -3.866408   
...                           ...                          ...       ...   
2022-06-06 04:45:00  [1, 1, 2, 1]   [True, False, False, True] -3.451396   
2022-06-06 05:00:00  [1, 1, 2, 1]   [True, False, False, True] -4.759148   
2022-06-06 05:15:00  [1, 1, 2, 1]   [True, False, False, True] -4.996401   
2022-06-06 05:30:00  [1, 1, 2, 1]   [True, False, False, True] -4.886483   
2022-06-06 05:45:00  [1, 1, 2, 1]   [True, False, False, True] -4.529248   

                     load_reward  EV_reward   rewards  
time                                                   
2022-01-01 00:00:00    -5.171626        0.0 -5.171626  
2022-01-01 00:15:00    -5.859286        0.0 -5.859286  
2022-01-01 00:30:00    -2.588349        0.0 -2.588349  
2022-01-01 00:45:00    -4.777347        0.0 -4.777347  
2022-01-01 01:00:00    -5.454616        0.0 -5.454616  
...                          ...        ...       ...  
2022-06-06 04:45:00    -5.690134        0.0 -5.690134  
2022-06-06 05:00:00    -5.905819        0.0 -5.905819  
2022-06-06 05:15:00    -5.805893        0.0 -5.805893  
2022-06-06 05:30:00    -5.481134        0.0 -5.481134  
2022-06-06 05:45:00    -6.207462        0.0 -6.207462  

[15000 rows x 11 columns]

In [ ]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [ ]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 7302, Arrival time: 2022-01-01 12:15:00, Parking_time: 23.337668735525614, Leaving_time: 2022-01-02 11:35:15.607448, SOC: 0.7043439468302471, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 8344, Arrival time: 2022-12-31 11:15:00, Parking_time: 22.761793034207425, Leaving_time: 2023-01-01 10:00:42.454923, SOC: 0.2753454133017793, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8679.12 , over-consume=kWh  32381.53 , under-consume=kWh  23702.41 , Total_cost=€  486.36 , overcost=€  1361.11 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8478.06 , over-consume=kWh  32572.26 , under-consume=kWh  24094.2 , Total_cost=€  460.99 , overcost=€  1351.5 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -9289.91 , over-consume=KWh  1148.84 , under-consume=KWh  10438.75 , Total_cost=€  -332.84 , Overcost=€  49.35 
 EV_INFO: Av.EV_energy_leaving=kWh  74.32 , Std.EV_energy_leaving=kWh  22.59 , EV_departures =  1040 , EV_queue_left =  0
SCORE:  Cumulative_reward= 393317.44 - Step_rewars (load_t= 328360.43, EVs_energy_t= 38448.61)
 - Final_rewards (EVs_energy= 18442.34, Overconsume= -623.29, Underconsume= -4373.39, Overcost= 13062.73)
Episode:1 Score:393317.43637863797


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(14995)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 03:30:00  84.613106  34.289143  59.348557  58.065849   
2022-06-06 03:45:00  85.117523  34.039143  59.852974  58.570267   
2022-06-06 04:00:00  85.117523  33.789143  60.772327  59.489620   
2022-06-06 04:15:00  85.117523  33.539143  61.604851  60.322144   
2022-06-06 04:30:00  85.117523  33.289143  62.534466  61.251759   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                       ...           ...   
2022-06-06 03:30:00  [9834, 9835, 9836, 9837]  [1, 2, 1, 1]   
2022-06-06 03:45:00  [9834, 9835, 9836, 9837]  [0, 2, 1, 1]   
2022-06-06 04:00:00  [9834, 9835, 9836, 9837]  [0, 2, 1, 1]   
2022-06-06 04:15:00  [9834, 9835, 9836, 9837]  [0, 2, 1, 1]   
2022-06-06 04:30:00  [9834, 9835, 9836, 9837]  [0, 2, 1, 1]   

                                      mask_truth          load  load_reward  \
time                                                                          
2022-01-01 00:00:00  [False, False, False, True] -3.331459e+00    -4.032045   
2022-01-01 00:15:00  [False, False, False, True] -3.419227e+00    -4.919281   
2022-01-01 00:30:00  [False, False, False, True] -3.951569e+00    -3.813677   
2022-01-01 00:45:00  [False, False, False, True] -3.288206e+00    -6.152067   
2022-01-01 01:00:00   [False, True, False, True] -5.267273e+00    -5.415089   
...                                          ...           ...          ...   
2022-06-06 03:30:00    [True, False, True, True]  4.440892e-16    15.000000   
2022-06-06 03:45:00    [True, False, True, True]  0.000000e+00    15.000000   
2022-06-06 04:00:00    [True, False, True, True]  0.000000e+00    15.000000   
2022-06-06 04:15:00    [True, False, True, True]  0.000000e+00    15.000000   
2022-06-06 04:30:00    [True, False, True, True]  0.000000e+00    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -4.032045  
2022-01-01 00:15:00        0.0  -4.919281  
2022-01-01 00:30:00        0.0  -3.813677  
2022-01-01 00:45:00        0.0  -6.152067  
2022-01-01 01:00:00        0.0  -5.415089  
...                        ...        ...  
2022-06-06 03:30:00        0.0  15.000000  
2022-06-06 03:45:00        0.0  15.000000  
2022-06-06 04:00:00        0.0  15.000000  
2022-06-06 04:15:00        0.0  15.000000  
2022-06-06 04:30:00        0.0  15.000000  

[14995 rows x 11 columns]

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.close()